Berechnen des Verschattungsfaktors einer PV-Freiflächenanlage für ein Jahr aufgelöst in 5 Minuten

In [2]:
import pandas as pd
import pvlib

In [ ]:
# Inputs:

# Zeitraum
startdatum = "2025-01-01"
enddatum = "2025-12-31"

# Geometrie der PV-Anlage
modulneigung = 20  # Grad
modulazimut = 210  # Grad
hoehe_unterkante = 1  # Meter
hoehe_oberkante = 3  # Meter
reihenteilung = 4  # Meter
modullaenge = 3  # Meter

# Standort der PV-Anlage

#This will break the linter do to wrong spacing for the eaqual sign
breitengrad=47.99  # Grad

laengengrad = 16.86  # Grad

In [7]:
# Inputs überprüfen:

from utils import is_valid_date

# Added argument "None" in order for the program to not crash 
if not (is_valid_date(startdatum, None) and is_valid_date(enddatum, None)):
    print("Ungueltiges Datum!!!")

In [8]:
# Berechnung:

# Erstellen der 5-Minuten Zeitreihe eines Jahrs
df = pd.DataFrame(
    index=pd.date_range(start=startdatum, end=enddatum, freq="5min", tz="Europe/Vienna")
)

# Definition des Standorts
standort = pvlib.location.Location(breitengrad, laengengrad, "Europe/Vienna")

# Berechne den Sonnenstand für jeden Zeitpunkt
solar_position = pvlib.solarposition.get_solarposition(
    df.index, standort.latitude, standort.longitude, standort.altitude
)
# Berechne den Verschattungsfaktor für jeden Zeitpunkt
df["verschattungsfaktor"] = pvlib.shading.shaded_fraction1d(
    solar_zenith=solar_position["zenith"],
    solar_azimuth=solar_position["azimuth"],
    axis_azimuth=modulazimut - 90,
    shaded_row_rotation=modulneigung,
    shading_row_rotation=modulneigung,
    collector_width=modullaenge,
    pitch=reihenteilung,
    axis_tilt=0,
    surface_to_axis_offset=0,
    cross_axis_slope=0,
)

In [9]:
# Output:

# Visualisierung:
from newplot import plot

plot(
    df.index,
    df["verschattungsfaktor"],
    "Verschattungsfaktor",
    "Verschattungfaktor über das Jahr",
    "Zeit",
    "Faktor",
)